In [1]:
import robin_stocks.robinhood as rh
import pandas as pd
import requests
from datetime import datetime
import yfinance as yf
import time 
import math
import random

username ='liuweiwang0824@gmail.com'
password ='Umcqar45&M'

def login():
    rh.login(username, password)


login()

def open_market():
    time_now = datetime.now().time()
    market_open = datetime.time(9, 30, 0)
    market_close = datetime.time(15, 59, 0)
    return market_open < time_now < market_close

def get_cash():
    rh.login(username, password)
    rh_profile = rh.load_account_profile()
    return float(rh_profile['portfolio_cash'])
print(f'Buying power before making trade: {get_cash()}')

def get_holdings_and_bought_price(stocks):
    holdings = {stock: 0 for stock in stocks}
    bought_price = {stock: 0 for stock in stocks}
    rh_holdings = rh.account.build_holdings()
    for stock in stocks:
        holdings[stock] = int(float((rh_holdings.get(stock, {}).get('quantity', '0'))))
        bought_price[stock] = float((rh_holdings.get(stock, {}).get('average_buy_price', '0')))
    return holdings, bought_price

today = datetime.today()
a, b, c = str(today.year), str(today.month), str(today.day)

f1 = pd.read_csv(r'\\DESKTOP-RRDK2EH\Server\Users\jizha\Desktop\seabridge_datapool1\final_strategy_data_temporaly\\three_strategy_buy_point_' + a + '_' + b + '_' + c + '.csv')
# 移除带有点（"."）的股票代码
ticker_sum = f1['0'].tolist()

ticker_sum = [ticker for ticker in ticker_sum if "." not in ticker]
#ticker_sum.remove('RTWG.L')
#ticker_sum.remove('PPHC.L')
print(f"Total stock in pool: {len(ticker_sum)}")
 

def buy(stock, allowable_holdings):
    rh.orders.order_buy_fractional_by_price(stock, allowable_holdings, timeInForce='gfd', extendedHours=False)
 
def get_yahoo_historical_prices_5min(stock):
    data = yf.download(stock, interval='5m', period='2d', progress=False)
    if len(data) < 3:  # Ensure we have enough data points
        return None, None, None, None
    current_price = data['Close'].iloc[-1]  # Last data point
    price_5min = data['Close'].iloc[-2]  # Second last data point
    price_10min = data['Close'].iloc[-3]  # Third last data point
    
    # Extracting the previous day's close
    yesterday_data = data[data.index.date != data.index[-1].date()]
    close_p = yesterday_data['Close'].iloc[-1] if not yesterday_data.empty else None

    return current_price, price_5min, price_10min, close_p
def final_trade_stock_data(stocks):
    final_data = {}
    
    for stock in stocks:
        current_price, price_5min, price_10min, close_p = get_yahoo_historical_prices_5min(stock)
        if current_price is None or price_5min is None or price_10min is None or close_p is None:
            continue
        
        # Check if the stock meets the criteria
        if price_5min > price_10min and current_price > close_p:
            pct_change = ((current_price - close_p) / close_p) * 100
            if 0 < pct_change <5:
                final_data[stock] = {
                    'current_price': current_price,
                    'price_5min': price_5min,
                    'price_10min': price_10min,
                    'close_p': close_p,
                    'pct_change': pct_change
                }
    
    return final_data


selected_stocks = final_trade_stock_data(ticker_sum)

print(f"Selected stocks: {len(selected_stocks)}")
for stock, data in selected_stocks.items():
    print(f"{stock}:")
    print(f"  5-min price: ${data['price_5min']:.2f}")
    print(f"  10-min price: ${data['price_10min']:.2f}")
    print(f"  Previous close price: ${data['close_p']:.2f}")
    print(f"  Percentage change: {data['pct_change']:.2f}%")


def calculate_multiplicative_factor(change):
#    """根据市场变化计算乘法因子。"""
    return 40 + 40 * abs(change) / 0.03
    
def calculate_market_activity_coefficient(total_stocks, selected_stocks):
    """计算市场活跃度系数"""
    ratio = selected_stocks / total_stocks
    market_activity_coefficient = 0.6 / (1 + math.exp(-12 * (ratio - 0.5))) + 0.2
    market_activity_coefficient=round(market_activity_coefficient,2)

    return market_activity_coefficient
 
def calculate_total_buying_power(change, cash, total_stocks, selected_stocks):
    market_activity_coefficient = calculate_market_activity_coefficient(total_stocks, selected_stocks)
    print(f"Stock Pool Activity Coefficient: {market_activity_coefficient}")  # 打印市场活跃系数

    multiplicative_factor = calculate_multiplicative_factor(change)
    multiplicative_factor=round(multiplicative_factor)
    print(f"Multiplicative Factor: {multiplicative_factor}")  # 打印乘法因子

    adjustment_coefficient = 1 + change * multiplicative_factor
    total_buying_power_adjusted = adjustment_coefficient * cash * market_activity_coefficient
    total_buying_power_adjusted = max(0, total_buying_power_adjusted)
    if total_buying_power_adjusted > cash:
        total_buying_power_adjusted = cash
    
    return total_buying_power_adjusted

stocks = final_trade_stock_data(ticker_sum)
num_of_stocks = len(stocks)
print(f"Today's stock pick contains {num_of_stocks} stocks:")
def get_stock_change(stock):
    # 使用yfinance获取股票的最近两天的收盘价格
    data = yf.download(stock, period="2d", progress=False)['Close']
    if len(data) < 2:
        return None, None
    today_close, yesterday_close = data[-1], data[-2]
    change_percentage = (today_close - yesterday_close) / yesterday_close * 100
    return today_close, change_percentage

# 修改打印股票信息的部分：
for stock in stocks:
    current_price, change_pct = get_stock_change(stock)
    if current_price is None or change_pct is None:
        print(f"{stock}: Data not available")
        continue
    #print(f"{stock}: Current Price: ${current_price:.2f}, Change: {change_pct:.2f}%")

spy_current = yf.download("SPY", period="1d", progress=False)['Close'][-1]
qqq_current = yf.download("QQQ", period="1d", progress=False)['Close'][-1]
spy_previous_close = yf.download("SPY", period="2d", progress=False)['Close'][-2]
qqq_previous_close = yf.download("QQQ", period="2d", progress=False)['Close'][-2]
spy_change = (spy_current - spy_previous_close) / spy_previous_close
qqq_change = (qqq_current - qqq_previous_close) / qqq_previous_close
average_change = (spy_change + qqq_change)  

#print(f"SPY Change: {spy_change*100:.2f}%")
#print(f"QQQ Change: {qqq_change*100:.2f}%")
print(f"Market Optimism Factor: {average_change*100:.2f}")  # 打印SPY和QQQ的涨跌百分比

stocks = final_trade_stock_data(ticker_sum)

myCash = get_cash()
cash = calculate_total_buying_power(average_change, myCash, len(ticker_sum), len(stocks))
cash = round(cash) - 1
print('Buying power:')
print(cash)
if cash <= 0:
    print("Insufficient buying power. No trades will be executed.")
else:
 
    trade_dict = {stock: 0 for stock in stocks}
    price_dict = {stock: 0 for stock in stocks}
    df_trades = pd.DataFrame(columns=stocks)
    df_prices = pd.DataFrame(columns=stocks)

    #prices = rh.stocks.get_latest_price(stocks)
    holdings, bought_price = get_holdings_and_bought_price(stocks)
    # Modify the check_purchase_successful function to check the holdings directly
    def check_purchase_successful(stock):
        holdings_after_purchase, _ = get_holdings_and_bought_price([stock])
        return holdings_after_purchase[stock] > 0  # Check if we hold any of the stock

    for stock in stocks:
        allowable_holdings = round(cash / len(stocks), 1)
        print(f"Attempting to buy {stock}:")
        print(f"Funds allocated: ${allowable_holdings}")

        # Place the market order
        buy(stock, allowable_holdings)

        # Pause for 3 seconds to allow the broker to process the order
        time_to_sleep = random.uniform(5, 12)
                                
        time.sleep(time_to_sleep)

        # Check if purchase was successful
    #    attempts = 1
    #    while not check_purchase_successful(stock) and attempts < 1:  # Limit to 2 attempts
    #        print(f"Purchase of {stock} failed. Retrying...")
    #        buy(stock, allowable_holdings)

            # Pause for 3 seconds again
    #        time.sleep(3)

    #        attempts += 1

     #   if attempts == 1:
     #       print(f"Failed to buy {stock} after 1 attempt.")


    #-----------#
    time.sleep(time_to_sleep)

    print(f'Buying power after making trade: {get_cash()}')


#ToolBox
#quantity = 11.11 # convert quantity to float once
#s='A'   
#rh.orders.order_sell_market(symbol=s, quantity=quantity, timeInForce='gfd')
    

ERROR: There was an issue loading pickle file. Authentication may be expired - logging in normally.


KeyError: 'detail'

In [ ]:
 import robin_stocks.robinhood as rh
import pandas as pd
import time

username = 'liuweiwang0824@gmail.com'
password = 'Umcqar45&M'

# 登录
def login():
    rh.login(username, password)

login()

# 获取现金余额
def get_cash():
    rh_profile = rh.load_account_profile()
    return float(rh_profile['portfolio_cash'])

# 买入指定股票
def buy(stock, allowable_holdings):
    rh.orders.order_buy_fractional_by_price(stock, allowable_holdings, timeInForce='gfd', extendedHours=False)

# 计算买入每只股票的金额
def calculate_allowable_holdings(cash, stocks):
    return round(cash / len(stocks), 2)

# 主流程
def main():
    selected_stocks = ['BX', 'LOW', 'GRMN', 'AIG', 'AOS', 'WSM', 'LECO']
    cash = get_cash()
    allowable_cash = round(cash / 2, 2)  # 使用购买力的一半
    print(f'Buying power to be used: ${allowable_cash}')
    
    allowable_holdings = calculate_allowable_holdings(allowable_cash, selected_stocks)
    print(f'Funds allocated per stock: ${allowable_holdings}')
    
    if allowable_holdings <= 0:
        print("Insufficient buying power. No trades will be executed.")
        return
    
    for stock in selected_stocks:
        print(f"Attempting to buy {stock}:")
        buy(stock, allowable_holdings)
        print(f"Bought {stock} with ${allowable_holdings}")
        time.sleep(120)  # 每次买入后间隔2分钟
    
    print(f'Buying power after making trade: {get_cash()}')

if __name__ == "__main__":
    main()


In [ ]:
import robin_stocks.robinhood as rh

username = 'liuweiwang0824@gmail.com'
password = 'Umcqar45&M'

# 登录
def login():
    rh.login(username, password)

login()

# 获取指定股票的持仓数量
def get_stock_holdings(stock):
    rh_holdings = rh.account.build_holdings()
    holdings = int(float(rh_holdings.get(stock, {}).get('quantity', '0')))
    return holdings

# 主流程
def main(stock):
    shares = get_stock_holdings(stock)
    print(f'You hold {shares} shares of {stock}.')

if __name__ == "__main__":
    stock_to_check = 'BX'  # 在这里替换为您想要检查的股票代码
    main(stock_to_check)


In [ ]:
import robin_stocks.robinhood as rh
import pandas as pd
import time

username = 'liuweiwang0824@gmail.com'
password = 'Umcqar45&M'

# 登录
def login():
    rh.login(username, password)

login()

# 获取现金余额
def get_cash():
    rh_profile = rh.load_account_profile()
    return float(rh_profile['portfolio_cash'])

# 买入指定股票
def buy(stock, allowable_holdings):
    rh.orders.order_buy_fractional_by_price(stock, allowable_holdings, timeInForce='gfd', extendedHours=False)

# 获取持仓和买入价格
def get_holdings_and_bought_price(stocks):
    holdings = {stock: 0 for stock in stocks}
    rh_holdings = rh.account.build_holdings()
    for stock in stocks:
        holdings[stock] = int(float(rh_holdings.get(stock, {}).get('quantity', '0')))
    return holdings

# 计算买入每只股票的金额
def calculate_allowable_holdings(cash, stocks):
    return round(cash / len(stocks), 2)

# 检查是否成功买入
def check_purchase_successful(stock, initial_holdings):
    current_holdings = get_holdings_and_bought_price([stock])
    return current_holdings[stock] > initial_holdings[stock]

ticker = ["APD", "GD", "MA", "MDLZ", "PG", "VRSN"]
# 主流程
def main():
    selected_stocks = tickers
    cash = get_cash()
    allowable_cash = round(cash / 1.5, 2)  # 使用购买力的一半
    print(f'Buying power to be used: ${allowable_cash}')
    
    allowable_holdings = calculate_allowable_holdings(allowable_cash, selected_stocks)
    print(f'Funds allocated per stock: ${allowable_holdings}')
    
    if allowable_holdings <= 0:
        print("Insufficient buying power. No trades will be executed.")
        return
    
    failed_purchases = []
    for stock in selected_stocks:
        print(f"Attempting to buy {stock}:")
        initial_holdings = get_holdings_and_bought_price([stock])
        success = False
        for attempt in range(3):
            buy(stock, allowable_holdings)
            time.sleep(30)  # 等待30秒后检查持仓
            if check_purchase_successful(stock, initial_holdings):
                print(f"Successfully bought {stock} with ${allowable_holdings} on attempt {attempt + 1}")
                success = True
                break
            else:
                print(f"Attempt {attempt + 1} to buy {stock} failed.")
        if not success:
            failed_purchases.append(stock)
            print(f"Failed to buy {stock} after 3 attempts. Needs manual purchase.")
        time.sleep(90)  # 每次买入后间隔2分钟（包括30秒检查时间）
    
    print(f'Buying power after making trade: {get_cash()}')
    if failed_purchases:
        print("The following stocks need manual purchase:")
        for stock in failed_purchases:
            print(stock)

if __name__ == "__main__":
    main()


In [ ]:
import robin_stocks.robinhood as rh

username = 'liuweiwang0824@gmail.com'
password = 'Umcqar45&M'

# 登录
def login():
    rh.login(username, password)

login()

# 获取指定股票的持仓数量
def get_stock_holdings(stock):
    rh_holdings = rh.account.build_holdings()
    holdings = int(float(rh_holdings.get(stock, {}).get('quantity', '0')))
    return holdings

# 主流程
def main(stock):
    shares = get_stock_holdings(stock)
    print(f'You hold {shares} shares of {stock}.')

if __name__ == "__main__":
    stock_to_check = 'AOS'  # 在这里替换为您想要检查的股票代码
    main(stock_to_check)
